In [1]:
import numpy as np
import matplotlib.pyplot as plt


In [2]:

import pickle
import os
import sys

In [3]:
class parse_input():
    def __init__(self,experiment_index,data_type,batch_size,initial_size,iterations,method,experiment_folder,method2,gpu,initial_idx_path=None):
        self.experiment_index = experiment_index
        self.data_type = data_type
        self.batch_size = batch_size
        self.initial_size = initial_size
        self.iterations = iterations
        self.method = method
        self.experiment_folder = experiment_folder
        self.method2 = method2
        self.gpu = gpu
        self.initial_idx_path = initial_idx_path

In [4]:

def load_batch(fpath, label_key='labels'):

    with open(fpath, 'rb') as f:
        if sys.version_info < (3,):
            d = pickle.load(f)
        else:
            d = pickle.load(f, encoding='bytes')
            # decode utf8
            d_decoded = {}
            for k, v in d.items():
                d_decoded[k.decode('utf8')] = v
            d = d_decoded
    data = d['data']
    labels = d[label_key]

    data = data.reshape(data.shape[0], 3, 32, 32)
    return data, labels

In [5]:
from keras.datasets import mnist
from keras.datasets import cifar100
from keras.datasets import cifar10

Using TensorFlow backend.


In [6]:
def load_mnist():
    """
    load and pre-process the MNIST data
    """

    from keras.datasets import mnist
    (x_train, y_train), (x_test, y_test) = mnist.load_data()

    if K.image_data_format() == 'channels_last':
        x_train = x_train.reshape((x_train.shape[0], 28, 28, 1))
        x_test = x_test.reshape((x_test.shape[0], 28, 28, 1))
    else:
        x_train = x_train.reshape((x_train.shape[0], 1, 28, 28))
        x_test = x_test.reshape((x_test.shape[0], 1, 28, 28))

    # standardise the dataset:
    x_train = np.array(x_train).astype('float32') / 255
    x_test = np.array(x_test).astype('float32') / 255

    # shuffle the data:
    perm = np.random.permutation(x_train.shape[0])
    x_train = x_train[perm]
    y_train = y_train[perm]

    return (x_train, y_train), (x_test, y_test)


In [7]:
def evaluate_sample(training_function, X_train, Y_train, X_test, Y_test, checkpoint_path):
    """
    A function that accepts a labeled-unlabeled data split and trains the relevant model on the labeled data, returning
    the model and it's accuracy on the test set.
    """

    # shuffle the training set:
    perm = np.random.permutation(X_train.shape[0])
    X_train = X_train[perm]
    Y_train = Y_train[perm]

    # create the validation set:
    X_validation = X_train[:int(0.2*X_train.shape[0])]
    Y_validation = Y_train[:int(0.2*Y_train.shape[0])]
    X_train = X_train[int(0.2*X_train.shape[0]):]
    Y_train = Y_train[int(0.2*Y_train.shape[0]):]

    # train and evaluate the model:
    model = training_function(X_train, Y_train, X_validation, Y_validation, checkpoint_path, gpu=args.gpu)
    if args.data_type in ['imdb', 'wiki']:
        acc = model.evaluate(X_test, Y_test, verbose=0)
    else:
        loss, acc = model.evaluate(X_test, Y_test, verbose=0)

    return acc, model

In [8]:
from models import *
from query_methods import *

##数据集一
#初始化参数集 数据集为mnist，考虑到内存较小，而gpu和cpu=运行速度较快，将batch_size设置为1

In [9]:
experiment_index = 0
data_type = 'mnist'
batch_size = 1
initial_size = 100
iterations = 20
method = 'DiscriminativeLearned'
experiment_folder = r'C:\Users\76113\Desktop\active_learning'
method2 = 'Random'
gpu = 1
args = parse_input(experiment_index,data_type,batch_size,initial_size,iterations,method,experiment_folder,method2,gpu)

In [10]:
type(args.initial_size)

int

In [14]:
#load dataset
if args.data_type == 'mnist':
    (X_train, Y_train), (X_test, Y_test) = load_mnist()
    num_labels = 10
    if K.image_data_format() == 'channels_last':
        input_shape = (28, 28, 1)
    else:
        input_shape = (1, 28, 28)
    evaluation_function = train_mnist_model
if args.data_type == 'cifar10':
    (X_train, Y_train), (X_test, Y_test) = load_cifar_10()
    num_labels = 10
    if K.image_data_format() == 'channels_last':
        input_shape = (32, 32, 3)
    else:
        input_shape = (3, 32, 32)
    evaluation_function = train_cifar10_model
if args.data_type == 'cifar100':
    (X_train, Y_train), (X_test, Y_test) = load_cifar_100()
    num_labels = 100
    if K.image_data_format() == 'channels_last':
        input_shape = (32,32,3)
    else:
        input_shape = (3, 32, 32)
    evaluation_function = train_cifar100_model




In [15]:
# make categorical:
Y_train = to_categorical(Y_train)
Y_test = to_categorical(Y_test)



In [16]:
# set the first query method:
if args.method == 'Random':
    method = RandomSampling
elif args.method == 'CoreSet':
    method = CoreSetSampling
elif args.method == 'CoreSetMIP':
    method = CoreSetMIPSampling
elif args.method == 'Discriminative':
    method = DiscriminativeSampling
elif args.method == 'DiscriminativeLearned':
    method = DiscriminativeRepresentationSampling
elif args.method == 'DiscriminativeAE':
    method = DiscriminativeAutoencoderSampling
elif args.method == 'DiscriminativeStochastic':
    method = DiscriminativeStochasticSampling
elif args.method == 'Uncertainty':
    method = UncertaintySampling
elif args.method == 'Bayesian':
    method = BayesianUncertaintySampling
elif args.method == 'UncertaintyEntropy':
    method = UncertaintyEntropySampling
elif args.method == 'BayesianEntropy':
    method = BayesianUncertaintyEntropySampling
elif args.method == 'EGL':
    method = EGLSampling
elif args.method == 'Adversarial':
    method = AdversarialSampling

# set the second query method:
if args.method2 is not None:
    print("Using Two Methods...")
    if args.method2 == 'Random':
        method2 = RandomSampling
    elif args.method2 == 'CoreSet':
        method2 = CoreSetSampling
    elif args.method2 == 'CoreSetMIP':
        method2 = CoreSetMIPSampling
    elif args.method2 == 'Discriminative':
        method2 = DiscriminativeSampling
    elif args.method2 == 'DiscriminativeLearned':
        method2 = DiscriminativeRepresentationSampling
    elif args.method2 == 'DiscriminativeAE':
        method2 = DiscriminativeAutoencoderSampling
    elif args.method2 == 'DiscriminativeStochastic':
        method2 = DiscriminativeStochasticSampling
    elif args.method2 == 'Uncertainty':
        method2 = UncertaintySampling
    elif args.method2 == 'Bayesian':
        method2 = BayesianUncertaintySampling
    elif args.method2 == 'UncertaintyEntropy':
        method2 = UncertaintyEntropySampling
    elif args.method2 == 'BayesianEntropy':
        method2 = BayesianUncertaintyEntropySampling
    elif args.method2 == 'EGL':
        method2 = EGLSampling
    elif args.method2 == 'Adversarial':
        method2 = AdversarialSampling
    else:
        print("ERROR - UNKNOWN SECOND METHOD!")
        exit()
else:
    method2 = None
    print("Only One Method Used...")

Using Two Methods...


In [17]:
# create the results path:
if not os.path.isdir(os.path.join(args.experiment_folder, 'results')):
    os.mkdir(os.path.join(args.experiment_folder, 'results'))
results_folder = os.path.join(args.experiment_folder, 'results')
if method2 is None:
    results_path = os.path.join(results_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}.pkl'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    results_path = os.path.join(results_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}.pkl'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))

In [18]:
# create the label entropy path:
if method2 is None:
    entropy_path = os.path.join(results_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}_entropy.pkl'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    entropy_path = os.path.join(results_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}_entropy.pkl'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))

In [19]:
# create the checkpoint path:
if not os.path.isdir(os.path.join(args.experiment_folder, 'models')):
    os.mkdir(os.path.join(args.experiment_folder, 'models'))
model_folder = os.path.join(args.experiment_folder, 'models')
if method2 is None:
    checkpoint_path = os.path.join(model_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}.hdf5'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    checkpoint_path = os.path.join(model_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}.hdf5'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))


In [20]:
# load the indices:

labeled_idx = np.random.choice(X_train.shape[0], args.initial_size, replace=False)
# create the QueryMethod object:
if method2 is not None:
    query_method = CombinedSampling(None, input_shape, num_labels, method, method2, args.gpu)
else:
    query_method = method(None, input_shape, num_labels, args.gpu)

In [21]:
from tensorflow.compat.v1 import ConfigProto
from tensorflow.compat.v1 import InteractiveSession

config = ConfigProto()
config.gpu_options.allow_growth = True
session = InteractiveSession(config=config)


In [22]:
from tensorflow.compat.v1 import ConfigProto
from tensorflow.compat.v1 import InteractiveSession

config = ConfigProto()
config.gpu_options.allow_growth = True
session = InteractiveSession(config=config)


C:\E\lib\site-packages\tensorflow_core\python\client\session.py:1752: UserWarning: An interactive session is already active. This can cause out-of-memory errors in some cases. You must explicitly call `InteractiveSession.close()` to release resources held by the other session(s).
  warnings.warn('An interactive session is already active. This can '


In [23]:
# run the experiment:
accuracies = []
entropies = []
label_distributions = []
queries = []
acc, model = evaluate_sample(evaluation_function, X_train[labeled_idx,:], Y_train[labeled_idx], X_test, Y_test, checkpoint_path)
query_method.update_model(model)
accuracies.append(acc)
print("Test Accuracy Is " + str(acc))
for i in range(args.iterations):

    # get the new indices from the algorithm
    old_labeled = np.copy(labeled_idx)
    labeled_idx = query_method.query(X_train, Y_train, labeled_idx, args.batch_size)

    # calculate and store the label entropy:
    new_idx = labeled_idx[np.logical_not(np.isin(labeled_idx, old_labeled))]
    new_labels = Y_train[new_idx]
    new_labels /= np.sum(new_labels)
    new_labels = np.sum(new_labels, axis=0)
    entropy = -np.sum(new_labels * np.log(new_labels + 1e-10))
    entropies.append(entropy)
    label_distributions.append(new_labels)
    queries.append(new_idx)

    # evaluate the new sample:
    acc, model = evaluate_sample(evaluation_function, X_train[labeled_idx], Y_train[labeled_idx], X_test, Y_test, checkpoint_path)
    query_method.update_model(model)
    accuracies.append(acc)
    print("Test Accuracy Is " + str(acc))


Train on 80 samples, validate on 20 samples
Epoch 1/150
 - 5s - loss: 2.2918 - accuracy: 0.1000 - val_loss: 2.1861 - val_accuracy: 0.4000
Epoch 2/150
 - 0s - loss: 2.1557 - accuracy: 0.3000 - val_loss: 2.1092 - val_accuracy: 0.4500
Epoch 3/150
 - 0s - loss: 2.0757 - accuracy: 0.3500 - val_loss: 2.0220 - val_accuracy: 0.4000
Epoch 4/150
 - 0s - loss: 1.9458 - accuracy: 0.4000 - val_loss: 1.8889 - val_accuracy: 0.5000
Epoch 5/150
 - 0s - loss: 1.8180 - accuracy: 0.4875 - val_loss: 1.7338 - val_accuracy: 0.7000
Epoch 6/150
 - 0s - loss: 1.5423 - accuracy: 0.6375 - val_loss: 1.5667 - val_accuracy: 0.7000
Epoch 7/150
 - 0s - loss: 1.4510 - accuracy: 0.6000 - val_loss: 1.3460 - val_accuracy: 0.7500
Epoch 8/150
 - 0s - loss: 1.3298 - accuracy: 0.5375 - val_loss: 1.1858 - val_accuracy: 0.7500
Epoch 9/150
 - 0s - loss: 0.9541 - accuracy: 0.7875 - val_loss: 1.0672 - val_accuracy: 0.7000
Epoch 10/150
 - 0s - loss: 0.9261 - accuracy: 0.7250 - val_loss: 0.9632 - val_accuracy: 0.7000
Epoch 11/150
 -


Epoch 00064: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 66/150
 - 0s - loss: 0.0103 - accuracy: 1.0000 - val_loss: 0.9630 - val_accuracy: 0.7500

Epoch 00065: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 67/150
 - 0s - loss: 0.0151 - accuracy: 1.0000 - val_loss: 0.9785 - val_accuracy: 0.7500

Epoch 00066: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 68/150
 - 0s - loss: 0.0111 - accuracy: 1.0000 - val_loss: 0.9921 - val_accuracy: 0.7500

Epoch 00067: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 69/150
 - 0s - loss: 0.0047 - accuracy: 1.000

Epoch 97/150
 - 0s - loss: 0.0113 - accuracy: 1.0000 - val_loss: 1.1500 - val_accuracy: 0.7500

Epoch 00096: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 98/150
 - 0s - loss: 0.0281 - accuracy: 0.9875 - val_loss: 1.2229 - val_accuracy: 0.7500

Epoch 00097: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 99/150
 - 0s - loss: 0.0265 - accuracy: 0.9875 - val_loss: 1.3886 - val_accuracy: 0.7000

Epoch 00098: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 100/150
 - 0s - loss: 0.0078 - accuracy: 1.0000 - val_loss: 1.4855 - val_accuracy: 0.7000

Epoch 00099: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\Dis


Epoch 00127: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 129/150
 - 0s - loss: 0.0109 - accuracy: 1.0000 - val_loss: 0.8794 - val_accuracy: 0.7500

Epoch 00128: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 130/150
 - 0s - loss: 0.0053 - accuracy: 1.0000 - val_loss: 0.9506 - val_accuracy: 0.7500

Epoch 00129: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 131/150
 - 0s - loss: 0.0035 - accuracy: 1.0000 - val_loss: 1.0195 - val_accuracy: 0.7500

Epoch 00130: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 132/150
 - 0s - loss: 0.0064 - accuracy: 1

Epoch 25/150
 - 0s - loss: 0.2555 - accuracy: 0.9125 - val_loss: 0.7744 - val_accuracy: 0.7500
Epoch 26/150
 - 0s - loss: 0.1766 - accuracy: 0.9625 - val_loss: 0.7890 - val_accuracy: 0.8000
Epoch 27/150
 - 0s - loss: 0.2492 - accuracy: 0.9375 - val_loss: 0.8277 - val_accuracy: 0.8000
Epoch 28/150
 - 0s - loss: 0.1893 - accuracy: 0.9750 - val_loss: 0.8433 - val_accuracy: 0.7500
Epoch 29/150
 - 0s - loss: 0.1506 - accuracy: 0.9625 - val_loss: 0.8278 - val_accuracy: 0.7500
Epoch 30/150
 - 0s - loss: 0.1511 - accuracy: 0.9625 - val_loss: 0.8426 - val_accuracy: 0.8000
Epoch 31/150
 - 0s - loss: 0.1218 - accuracy: 0.9875 - val_loss: 0.9221 - val_accuracy: 0.8000
Epoch 32/150
 - 0s - loss: 0.1158 - accuracy: 0.9875 - val_loss: 0.9768 - val_accuracy: 0.7500
Epoch 33/150
 - 0s - loss: 0.1040 - accuracy: 0.9875 - val_loss: 0.9514 - val_accuracy: 0.7500
Epoch 34/150
 - 0s - loss: 0.0921 - accuracy: 1.0000 - val_loss: 0.9400 - val_accuracy: 0.7500
Epoch 35/150
 - 0s - loss: 0.0992 - accuracy: 0.97

...


Epoch 00140: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 142/150
 - 0s - loss: 0.0023 - accuracy: 1.0000 - val_loss: 1.1870 - val_accuracy: 0.7000

Epoch 00141: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 143/150
 - 0s - loss: 0.0067 - accuracy: 1.0000 - val_loss: 1.2296 - val_accuracy: 0.7000

Epoch 00142: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 144/150
 - 0s - loss: 0.0047 - accuracy: 1.0000 - val_loss: 1.2264 - val_accuracy: 0.7000

Epoch 00143: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 145/150
 - 0s - loss: 0.0042 - accuracy: 1


Epoch 00054: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 56/150
 - 0s - loss: 0.0270 - accuracy: 1.0000 - val_loss: 0.1835 - val_accuracy: 0.9500

Epoch 00055: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 57/150
 - 0s - loss: 0.0250 - accuracy: 1.0000 - val_loss: 0.1858 - val_accuracy: 0.9500

Epoch 00056: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 58/150
 - 0s - loss: 0.0089 - accuracy: 1.0000 - val_loss: 0.1930 - val_accuracy: 0.9500

Epoch 00057: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 59/150
 - 0s - loss: 0.0156 - accuracy: 1.000

Epoch 87/150
 - 0s - loss: 0.0106 - accuracy: 1.0000 - val_loss: 0.2151 - val_accuracy: 0.9500

Epoch 00086: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 88/150
 - 0s - loss: 0.0334 - accuracy: 0.9875 - val_loss: 0.2001 - val_accuracy: 0.9500

Epoch 00087: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 89/150
 - 0s - loss: 0.0203 - accuracy: 0.9875 - val_loss: 0.1970 - val_accuracy: 0.9500

Epoch 00088: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 90/150
 - 0s - loss: 0.0172 - accuracy: 1.0000 - val_loss: 0.1979 - val_accuracy: 0.9500

Epoch 00089: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\Disc


Epoch 00117: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 119/150
 - 0s - loss: 0.0270 - accuracy: 0.9875 - val_loss: 0.1220 - val_accuracy: 0.9500

Epoch 00118: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 120/150
 - 0s - loss: 0.0052 - accuracy: 1.0000 - val_loss: 0.1102 - val_accuracy: 0.9500

Epoch 00119: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 121/150
 - 0s - loss: 0.0032 - accuracy: 1.0000 - val_loss: 0.0990 - val_accuracy: 0.9500

Epoch 00120: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Epoch 122/150
 - 0s - loss: 0.0114 - accuracy: 1


Epoch 00149: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_mnist_100_1_0.hdf5
Test Accuracy Is 0.8384000062942505


In [24]:

# save the results:

with open(results_path, 'wb') as f:

    pickle.dump([accuracies, args.initial_size, args.batch_size], f)

    print("Saved results to " + results_path)

with open(entropy_path, 'wb') as f:

    pickle.dump([entropies, label_distributions, queries], f)

    print("Saved entropy statistics to " + entropy_path)

Saved results to C:\Users\76113\Desktop\active_learning\results\DiscriminativeLearned_Random_mnist_100_1_0.pkl
Saved entropy statistics to C:\Users\76113\Desktop\active_learning\results\DiscriminativeLearned_Random_mnist_100_1_0_entropy.pkl


##数据集二 
#初始化参数集 数据集为cifar_10，考虑到内存较小，而gpu和cpu=运行速度较快，将batch_size设置为1

In [25]:
experiment_index = 0
data_type = 'cifar10'
batch_size = 1
initial_size = 100
iterations = 20
method = 'DiscriminativeLearned'
experiment_folder = r'C:\Users\76113\Desktop\active_learning'
method2 = 'Random'
gpu = 1
args = parse_input(experiment_index,data_type,batch_size,initial_size,iterations,method,experiment_folder,method2,gpu)


In [26]:
# (x_train, y_train), (x_test, y_test) = cifar10.load_data()
# X_train = x_train
# Y_train = y_train 
# X_test = x_test
# Y_test = y_test

In [27]:


def load_cifar_10():
    """
    load and pre-process the CIFAR-10 data
    """

    dirname = r'C:\Users\76113\Desktop\active_learning\data\cifar10'  

    num_train_samples = 50000

    x_train = np.empty((num_train_samples, 3, 32, 32), dtype='uint8')
    y_train = np.empty((num_train_samples,), dtype='uint8')

    for i in range(1, 6):
        fpath = os.path.join(dirname, 'data_batch_' + str(i))
        (x_train[(i - 1) * 10000: i * 10000, :, :, :],
         y_train[(i - 1) * 10000: i * 10000]) = load_batch(fpath)

    fpath = os.path.join(dirname, 'test_batch')
    x_test, y_test = load_batch(fpath)

    y_train = np.reshape(y_train, (len(y_train), 1))
    y_test = np.reshape(y_test, (len(y_test), 1))

    # standardise the dataset:
    x_train = x_train.astype('float32') / 255
    x_test = x_test.astype('float32') / 255

    if K.image_data_format() == 'channels_last':
        x_train = x_train.transpose(0, 2, 3, 1)
        x_test = x_test.transpose(0, 2, 3, 1)

    # shuffle the data:
    perm = np.random.permutation(x_train.shape[0])
    x_train = x_train[perm]
    y_train = y_train[perm]

    return (x_train, y_train), (x_test, y_test)


def load_cifar_100(label_mode='fine'):
    """
    load and pre-process the CIFAR-100 data
    """

    dirname = ''  # TODO: your path here

    #fpath = os.path.join(dirname, 'train')
    #x_train, y_train = load_batch(fpath, label_key=label_mode + '_labels')

    fpath = os.path.join(dirname, 'test')
    x_test, y_test = load_batch(fpath, label_key=label_mode + '_labels')

    y_train = np.reshape(y_train, (len(y_train), 1))
    y_test = np.reshape(y_test, (len(y_test), 1))

    # standardise the dataset:
    x_train = np.array(x_train).astype('float32') / 255
    x_test = np.array(x_test).astype('float32') / 255

    if K.image_data_format() == 'channels_last':
        x_train = x_train.transpose(0, 2, 3, 1)
        x_test = x_test.transpose(0, 2, 3, 1)

    # shuffle the data:
    perm = np.random.permutation(x_train.shape[0])
    x_train = x_train[perm]
    y_train = y_train[perm]

    return (x_train, y_train), (x_test, y_test)



In [28]:
#load dataset
if args.data_type == 'mnist':
    (X_train, Y_train), (X_test, Y_test) = load_mnist()
    num_labels = 10
    if K.image_data_format() == 'channels_last':
        input_shape = (28, 28, 1)
    else:
        input_shape = (1, 28, 28)
    evaluation_function = train_mnist_model
if args.data_type == 'cifar10':
    (X_train, Y_train), (X_test, Y_test) = load_cifar_10()
    num_labels = 10
    if K.image_data_format() == 'channels_last':
        input_shape = (32, 32, 3)
    else:
        input_shape = (3, 32, 32)
    evaluation_function = train_cifar10_model
if args.data_type == 'cifar100':
    (X_train, Y_train), (X_test, Y_test) = load_cifar_100()
    num_labels = 100
    if K.image_data_format() == 'channels_last':
        input_shape = (32,32,3)
    else:
        input_shape = (3, 32, 32)
    evaluation_function = train_cifar100_model




In [29]:



# make categorical:
Y_train = to_categorical(Y_train)
Y_test = to_categorical(Y_test)



# set the first query method:
if args.method == 'Random':
    method = RandomSampling
elif args.method == 'CoreSet':
    method = CoreSetSampling
elif args.method == 'CoreSetMIP':
    method = CoreSetMIPSampling
elif args.method == 'Discriminative':
    method = DiscriminativeSampling
elif args.method == 'DiscriminativeLearned':
    method = DiscriminativeRepresentationSampling
elif args.method == 'DiscriminativeAE':
    method = DiscriminativeAutoencoderSampling
elif args.method == 'DiscriminativeStochastic':
    method = DiscriminativeStochasticSampling
elif args.method == 'Uncertainty':
    method = UncertaintySampling
elif args.method == 'Bayesian':
    method = BayesianUncertaintySampling
elif args.method == 'UncertaintyEntropy':
    method = UncertaintyEntropySampling
elif args.method == 'BayesianEntropy':
    method = BayesianUncertaintyEntropySampling
elif args.method == 'EGL':
    method = EGLSampling
elif args.method == 'Adversarial':
    method = AdversarialSampling

# set the second query method:
if args.method2 is not None:
    print("Using Two Methods...")
    if args.method2 == 'Random':
        method2 = RandomSampling
    elif args.method2 == 'CoreSet':
        method2 = CoreSetSampling
    elif args.method2 == 'CoreSetMIP':
        method2 = CoreSetMIPSampling
    elif args.method2 == 'Discriminative':
        method2 = DiscriminativeSampling
    elif args.method2 == 'DiscriminativeLearned':
        method2 = DiscriminativeRepresentationSampling
    elif args.method2 == 'DiscriminativeAE':
        method2 = DiscriminativeAutoencoderSampling
    elif args.method2 == 'DiscriminativeStochastic':
        method2 = DiscriminativeStochasticSampling
    elif args.method2 == 'Uncertainty':
        method2 = UncertaintySampling
    elif args.method2 == 'Bayesian':
        method2 = BayesianUncertaintySampling
    elif args.method2 == 'UncertaintyEntropy':
        method2 = UncertaintyEntropySampling
    elif args.method2 == 'BayesianEntropy':
        method2 = BayesianUncertaintyEntropySampling
    elif args.method2 == 'EGL':
        method2 = EGLSampling
    elif args.method2 == 'Adversarial':
        method2 = AdversarialSampling
    else:
        print("ERROR - UNKNOWN SECOND METHOD!")
        exit()
else:
    method2 = None
    print("Only One Method Used...")
    
    
# create the results path:
if not os.path.isdir(os.path.join(args.experiment_folder, 'results')):
    os.mkdir(os.path.join(args.experiment_folder, 'results'))
results_folder = os.path.join(args.experiment_folder, 'results')
if method2 is None:
    results_path = os.path.join(results_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}.pkl'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    results_path = os.path.join(results_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}.pkl'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))


# create the label entropy path:
if method2 is None:
    entropy_path = os.path.join(results_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}_entropy.pkl'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    entropy_path = os.path.join(results_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}_entropy.pkl'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))


# create the checkpoint path:
if not os.path.isdir(os.path.join(args.experiment_folder, 'models')):
    os.mkdir(os.path.join(args.experiment_folder, 'models'))
model_folder = os.path.join(args.experiment_folder, 'models')
if method2 is None:
    checkpoint_path = os.path.join(model_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}.hdf5'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    checkpoint_path = os.path.join(model_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}.hdf5'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))



# load the indices:

labeled_idx = np.random.choice(X_train.shape[0], args.initial_size, replace=False)
# create the QueryMethod object:
if method2 is not None:
    query_method = CombinedSampling(None, input_shape, num_labels, method, method2, args.gpu)
else:
    query_method = method(None, input_shape, num_labels, args.gpu)
    

Using Two Methods...


In [30]:
from tensorflow.compat.v1 import ConfigProto
from tensorflow.compat.v1 import InteractiveSession

config = ConfigProto()
config.gpu_options.allow_growth = True
session = InteractiveSession(config=config)


C:\E\lib\site-packages\tensorflow_core\python\client\session.py:1752: UserWarning: An interactive session is already active. This can cause out-of-memory errors in some cases. You must explicitly call `InteractiveSession.close()` to release resources held by the other session(s).
  warnings.warn('An interactive session is already active. This can '


In [ ]:
# run the experiment:
accuracies = []
entropies = []
label_distributions = []
queries = []
acc, model = evaluate_sample(evaluation_function, X_train[labeled_idx,:], Y_train[labeled_idx], X_test, Y_test, checkpoint_path)
query_method.update_model(model)
accuracies.append(acc)
print("Test Accuracy Is " + str(acc))
for i in range(args.iterations):

    # get the new indices from the algorithm
    old_labeled = np.copy(labeled_idx)
    labeled_idx = query_method.query(X_train, Y_train, labeled_idx, args.batch_size)

    # calculate and store the label entropy:
    new_idx = labeled_idx[np.logical_not(np.isin(labeled_idx, old_labeled))]
    new_labels = Y_train[new_idx]
    new_labels /= np.sum(new_labels)
    new_labels = np.sum(new_labels, axis=0)
    entropy = -np.sum(new_labels * np.log(new_labels + 1e-10))
    entropies.append(entropy)
    label_distributions.append(new_labels)
    queries.append(new_idx)

    # evaluate the new sample:
    acc, model = evaluate_sample(evaluation_function, X_train[labeled_idx], Y_train[labeled_idx], X_test, Y_test, checkpoint_path)
    query_method.update_model(model)
    accuracies.append(acc)
    print("Test Accuracy Is " + str(acc))


Train on 80 samples, validate on 20 samples
Epoch 1/400
 - 8s - loss: 6.2168 - accuracy: 0.1000 - val_loss: 4.5098 - val_accuracy: 0.1500
Epoch 2/400
 - 0s - loss: 5.2617 - accuracy: 0.2000 - val_loss: 4.5335 - val_accuracy: 0.1500
Epoch 3/400
 - 0s - loss: 5.4228 - accuracy: 0.1375 - val_loss: 4.5583 - val_accuracy: 0.1500
Epoch 4/400
 - 0s - loss: 6.1193 - accuracy: 0.0750 - val_loss: 4.5873 - val_accuracy: 0.1500
Epoch 5/400
 - 0s - loss: 5.6941 - accuracy: 0.1000 - val_loss: 4.6333 - val_accuracy: 0.1000
Epoch 6/400
 - 0s - loss: 5.7285 - accuracy: 0.1625 - val_loss: 4.7126 - val_accuracy: 0.1000
Epoch 7/400
 - 0s - loss: 5.7534 - accuracy: 0.1500 - val_loss: 4.8262 - val_accuracy: 0.1000
Epoch 8/400
 - 0s - loss: 5.8613 - accuracy: 0.0875 - val_loss: 4.9487 - val_accuracy: 0.0500
Epoch 9/400
 - 0s - loss: 5.1684 - accuracy: 0.1875 - val_loss: 5.0188 - val_accuracy: 0.0500
Epoch 10/400
 - 0s - loss: 5.5801 - accuracy: 0.1250 - val_loss: 5.0756 - val_accuracy: 0.0500
Epoch 11/400
 -

Epoch 65/400
 - 0s - loss: 4.1488 - accuracy: 0.4125 - val_loss: 7.5525 - val_accuracy: 0.1500

Epoch 00064: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 66/400
 - 0s - loss: 4.1837 - accuracy: 0.3750 - val_loss: 7.7195 - val_accuracy: 0.1500

Epoch 00065: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 67/400
 - 0s - loss: 4.3641 - accuracy: 0.3250 - val_loss: 7.9576 - val_accuracy: 0.1500

Epoch 00066: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 68/400
 - 0s - loss: 3.9716 - accuracy: 0.4625 - val_loss: 8.0586 - val_accuracy: 0.1500

Epoch 00067: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\model


Epoch 00095: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 97/400
 - 0s - loss: 4.0346 - accuracy: 0.4125 - val_loss: 8.2667 - val_accuracy: 0.2000

Epoch 00096: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 98/400
 - 0s - loss: 3.4693 - accuracy: 0.6250 - val_loss: 6.7839 - val_accuracy: 0.3500

Epoch 00097: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 99/400
 - 0s - loss: 3.7972 - accuracy: 0.5500 - val_loss: 6.7794 - val_accuracy: 0.2000

Epoch 00098: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 100/400
 - 0s - loss: 3.3342 - accura

Epoch 128/400
 - 0s - loss: 3.7359 - accuracy: 0.6375 - val_loss: 7.6991 - val_accuracy: 0.2500

Epoch 00127: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 129/400
 - 0s - loss: 3.3573 - accuracy: 0.6625 - val_loss: 10.2435 - val_accuracy: 0.1000

Epoch 00128: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 130/400
 - 0s - loss: 3.0609 - accuracy: 0.8125 - val_loss: 10.4677 - val_accuracy: 0.1500

Epoch 00129: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 131/400
 - 0s - loss: 3.1115 - accuracy: 0.7750 - val_loss: 9.4590 - val_accuracy: 0.2000

Epoch 00130: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning

 - 0s - loss: 2.9677 - accuracy: 0.8000 - val_loss: 9.4391 - val_accuracy: 0.3000

Epoch 00158: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 160/400
 - 0s - loss: 2.6236 - accuracy: 0.9125 - val_loss: 8.5268 - val_accuracy: 0.2000

Epoch 00159: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 161/400
 - 0s - loss: 2.6710 - accuracy: 0.8875 - val_loss: 7.4440 - val_accuracy: 0.2500

Epoch 00160: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 162/400
 - 0s - loss: 2.6237 - accuracy: 0.9125 - val_loss: 6.9967 - val_accuracy: 0.2500

Epoch 00161: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\Discrimi

...

Epoch 280/400
 - 0s - loss: 2.2993 - accuracy: 0.9625 - val_loss: 8.8619 - val_accuracy: 0.1500

Epoch 00279: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 281/400
 - 0s - loss: 2.2656 - accuracy: 0.9750 - val_loss: 9.2373 - val_accuracy: 0.0500

Epoch 00280: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 282/400
 - 0s - loss: 2.3029 - accuracy: 0.9750 - val_loss: 9.0376 - val_accuracy: 0.0500

Epoch 00281: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 283/400
 - 0s - loss: 2.4754 - accuracy: 0.8875 - val_loss: 8.7038 - val_accuracy: 0.1500

Epoch 00282: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\m

 - 0s - loss: 2.1971 - accuracy: 0.9750 - val_loss: 8.6125 - val_accuracy: 0.1500

Epoch 00310: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 312/400
 - 0s - loss: 2.1433 - accuracy: 1.0000 - val_loss: 8.5904 - val_accuracy: 0.2000

Epoch 00311: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 313/400
 - 0s - loss: 2.1881 - accuracy: 0.9750 - val_loss: 8.4992 - val_accuracy: 0.2500

Epoch 00312: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 314/400
 - 0s - loss: 2.1969 - accuracy: 0.9625 - val_loss: 8.3006 - val_accuracy: 0.2000

Epoch 00313: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\Discrimi


Epoch 00341: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 343/400
 - 0s - loss: 2.1744 - accuracy: 0.9875 - val_loss: 9.2195 - val_accuracy: 0.1500

Epoch 00342: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 344/400
 - 0s - loss: 2.1286 - accuracy: 0.9875 - val_loss: 9.1999 - val_accuracy: 0.1500

Epoch 00343: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 345/400
 - 0s - loss: 2.2210 - accuracy: 0.9375 - val_loss: 8.8246 - val_accuracy: 0.1500

Epoch 00344: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 346/400
 - 0s - loss: 2.1095 - acc

Epoch 374/400
 - 0s - loss: 2.0705 - accuracy: 0.9875 - val_loss: 7.5728 - val_accuracy: 0.1500

Epoch 00373: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 375/400
 - 0s - loss: 2.0883 - accuracy: 0.9750 - val_loss: 7.1709 - val_accuracy: 0.1500

Epoch 00374: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 376/400
 - 0s - loss: 2.0289 - accuracy: 1.0000 - val_loss: 6.9648 - val_accuracy: 0.1000

Epoch 00375: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 377/400
 - 0s - loss: 2.1152 - accuracy: 0.9750 - val_loss: 7.1831 - val_accuracy: 0.1000

Epoch 00376: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\m

Epoch 12/400
 - 0s - loss: 5.9829 - accuracy: 0.0625 - val_loss: 5.5519 - val_accuracy: 0.1000
Epoch 13/400
 - 0s - loss: 5.7000 - accuracy: 0.1625 - val_loss: 5.8564 - val_accuracy: 0.1000
Epoch 14/400
 - 0s - loss: 5.5948 - accuracy: 0.1500 - val_loss: 5.9274 - val_accuracy: 0.1000
Epoch 15/400
 - 0s - loss: 5.8808 - accuracy: 0.1125 - val_loss: 5.7223 - val_accuracy: 0.1000
Epoch 16/400
 - 0s - loss: 5.5810 - accuracy: 0.1125 - val_loss: 5.5884 - val_accuracy: 0.1000
Epoch 17/400
 - 0s - loss: 5.2410 - accuracy: 0.0750 - val_loss: 5.4999 - val_accuracy: 0.1000
Epoch 18/400
 - 0s - loss: 5.4767 - accuracy: 0.1125 - val_loss: 5.4016 - val_accuracy: 0.1000
Epoch 19/400
 - 0s - loss: 5.1817 - accuracy: 0.1500 - val_loss: 5.3580 - val_accuracy: 0.1000
Epoch 20/400
 - 0s - loss: 5.4405 - accuracy: 0.1500 - val_loss: 5.3796 - val_accuracy: 0.1000
Epoch 21/400
 - 0s - loss: 5.1459 - accuracy: 0.1375 - val_loss: 5.2651 - val_accuracy: 0.1000
Epoch 22/400
 - 0s - loss: 5.2264 - accuracy: 0.13

##数据集三
#初始化参数集 数据集为cifar_100，考虑到内存较小，而gpu和cpu=运行速度较快，将batch_size设置为1

In [ ]:
(X_train, Y_train), (X_test, Y_test) = cifar100.load_data()
num_labels = 100
if K.image_data_format() == 'channels_last':
    input_shape = (32,32,3)
else:
    input_shape = (3, 32, 32)
evaluation_function = train_cifar100_model


In [ ]:
type(X_train)

In [34]:


# make categorical:
Y_train = to_categorical(Y_train)
Y_test = to_categorical(Y_test)


In [35]:
# set the first query method:
if args.method == 'Random':
    method = RandomSampling
elif args.method == 'CoreSet':
    method = CoreSetSampling
elif args.method == 'CoreSetMIP':
    method = CoreSetMIPSampling
elif args.method == 'Discriminative':
    method = DiscriminativeSampling
elif args.method == 'DiscriminativeLearned':
    method = DiscriminativeRepresentationSampling
elif args.method == 'DiscriminativeAE':
    method = DiscriminativeAutoencoderSampling
elif args.method == 'DiscriminativeStochastic':
    method = DiscriminativeStochasticSampling
elif args.method == 'Uncertainty':
    method = UncertaintySampling
elif args.method == 'Bayesian':
    method = BayesianUncertaintySampling
elif args.method == 'UncertaintyEntropy':
    method = UncertaintyEntropySampling
elif args.method == 'BayesianEntropy':
    method = BayesianUncertaintyEntropySampling
elif args.method == 'EGL':
    method = EGLSampling
elif args.method == 'Adversarial':
    method = AdversarialSampling

# set the second query method:
if args.method2 is not None:
    print("Using Two Methods...")
    if args.method2 == 'Random':
        method2 = RandomSampling
    elif args.method2 == 'CoreSet':
        method2 = CoreSetSampling
    elif args.method2 == 'CoreSetMIP':
        method2 = CoreSetMIPSampling
    elif args.method2 == 'Discriminative':
        method2 = DiscriminativeSampling
    elif args.method2 == 'DiscriminativeLearned':
        method2 = DiscriminativeRepresentationSampling
    elif args.method2 == 'DiscriminativeAE':
        method2 = DiscriminativeAutoencoderSampling
    elif args.method2 == 'DiscriminativeStochastic':
        method2 = DiscriminativeStochasticSampling
    elif args.method2 == 'Uncertainty':
        method2 = UncertaintySampling
    elif args.method2 == 'Bayesian':
        method2 = BayesianUncertaintySampling
    elif args.method2 == 'UncertaintyEntropy':
        method2 = UncertaintyEntropySampling
    elif args.method2 == 'BayesianEntropy':
        method2 = BayesianUncertaintyEntropySampling
    elif args.method2 == 'EGL':
        method2 = EGLSampling
    elif args.method2 == 'Adversarial':
        method2 = AdversarialSampling
    else:
        print("ERROR - UNKNOWN SECOND METHOD!")
        exit()
else:
    method2 = None
    print("Only One Method Used...")
    
    
# create the results path:
if not os.path.isdir(os.path.join(args.experiment_folder, 'results')):
    os.mkdir(os.path.join(args.experiment_folder, 'results'))
results_folder = os.path.join(args.experiment_folder, 'results')
if method2 is None:
    results_path = os.path.join(results_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}.pkl'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    results_path = os.path.join(results_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}.pkl'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))


# create the label entropy path:
if method2 is None:
    entropy_path = os.path.join(results_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}_entropy.pkl'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    entropy_path = os.path.join(results_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}_entropy.pkl'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))


# create the checkpoint path:
if not os.path.isdir(os.path.join(args.experiment_folder, 'models')):
    os.mkdir(os.path.join(args.experiment_folder, 'models'))
model_folder = os.path.join(args.experiment_folder, 'models')
if method2 is None:
    checkpoint_path = os.path.join(model_folder, '{alg}_{datatype}_{init}_{batch_size}_{idx}.hdf5'.format(
        alg=args.method, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))
else:
    checkpoint_path = os.path.join(model_folder, '{alg}_{alg2}_{datatype}_{init}_{batch_size}_{idx}.hdf5'.format(
        alg=args.method, alg2=args.method2, datatype=args.data_type, batch_size=args.batch_size, init=args.initial_size, idx=args.experiment_index
    ))



# load the indices:

labeled_idx = np.random.choice(X_train.shape[0], args.initial_size, replace=False)
# create the QueryMethod object:
if method2 is not None:
    query_method = CombinedSampling(None, input_shape, num_labels, method, method2, args.gpu)
else:
    query_method = method(None, input_shape, num_labels, args.gpu)
    

Using Two Methods...


In [ ]:
  
# run the experiment:
# run the experiment:
# run the experiment:
# run the experiment:
accuracies = []
entropies = []
label_distributions = []
queries = []
acc, model = evaluate_sample(evaluation_function, X_train[labeled_idx,:], Y_train[labeled_idx], X_test, Y_test, checkpoint_path)
query_method.update_model(model)
accuracies.append(acc)
print("Test Accuracy Is " + str(acc))
for i in range(args.iterations):

    # get the new indices from the algorithm
    old_labeled = np.copy(labeled_idx)
    labeled_idx = query_method.query(X_train, Y_train, labeled_idx, args.batch_size)

    # calculate and store the label entropy:
    new_idx = labeled_idx[np.logical_not(np.isin(labeled_idx, old_labeled))]
    new_labels = Y_train[new_idx]
    new_labels /= np.sum(new_labels)
    new_labels = np.sum(new_labels, axis=0)
    entropy = -np.sum(new_labels * np.log(new_labels + 1e-10))
    entropies.append(entropy)
    label_distributions.append(new_labels)
    queries.append(new_idx)

    # evaluate the new sample:
    acc, model = evaluate_sample(evaluation_function, X_train[labeled_idx], Y_train[labeled_idx], X_test, Y_test, checkpoint_path)
    query_method.update_model(model)
    accuracies.append(acc)
    print("Test Accuracy Is " + str(acc))


Train on 80 samples, validate on 20 samples
Epoch 1/1000
 - 8s - loss: 8.3614 - accuracy: 0.0125 - val_loss: 6.7990 - val_accuracy: 0.0000e+00
Epoch 2/1000
 - 0s - loss: 7.8598 - accuracy: 0.0250 - val_loss: 6.7966 - val_accuracy: 0.0000e+00
Epoch 3/1000
 - 0s - loss: 8.4658 - accuracy: 0.0000e+00 - val_loss: 6.7977 - val_accuracy: 0.0000e+00
Epoch 4/1000
 - 0s - loss: 8.2942 - accuracy: 0.0250 - val_loss: 6.7997 - val_accuracy: 0.0000e+00
Epoch 5/1000
 - 0s - loss: 8.1918 - accuracy: 0.0125 - val_loss: 6.8009 - val_accuracy: 0.0000e+00
Epoch 6/1000
 - 0s - loss: 8.0621 - accuracy: 0.0125 - val_loss: 6.7999 - val_accuracy: 0.0000e+00
Epoch 7/1000
 - 0s - loss: 8.2541 - accuracy: 0.0125 - val_loss: 6.8001 - val_accuracy: 0.0000e+00
Epoch 8/1000
 - 0s - loss: 8.0354 - accuracy: 0.0250 - val_loss: 6.8000 - val_accuracy: 0.0000e+00
Epoch 9/1000
 - 0s - loss: 7.7361 - accuracy: 0.0125 - val_loss: 6.8006 - val_accuracy: 0.0000e+00
Epoch 10/1000
 - 0s - loss: 8.1146 - accuracy: 0.0125 - val_l


Epoch 00062: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 64/1000
 - 0s - loss: 7.3077 - accuracy: 0.0250 - val_loss: 6.8955 - val_accuracy: 0.0000e+00

Epoch 00063: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 65/1000
 - 0s - loss: 7.2584 - accuracy: 0.0250 - val_loss: 6.8980 - val_accuracy: 0.0000e+00

Epoch 00064: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 66/1000
 - 0s - loss: 7.3527 - accuracy: 0.0125 - val_loss: 6.9001 - val_accuracy: 0.0000e+00

Epoch 00065: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 67/1000
 - 0s - loss: 

 - 0s - loss: 7.2285 - accuracy: 0.0250 - val_loss: 6.9439 - val_accuracy: 0.0000e+00

Epoch 00093: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 95/1000
 - 0s - loss: 7.0178 - accuracy: 0.0375 - val_loss: 6.9445 - val_accuracy: 0.0000e+00

Epoch 00094: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 96/1000
 - 0s - loss: 7.1363 - accuracy: 0.0375 - val_loss: 6.9460 - val_accuracy: 0.0000e+00

Epoch 00095: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 97/1000
 - 0s - loss: 7.3632 - accuracy: 0.0375 - val_loss: 6.9461 - val_accuracy: 0.0000e+00

Epoch 00096: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning

Epoch 125/1000
 - 0s - loss: 7.2548 - accuracy: 0.0125 - val_loss: 6.9798 - val_accuracy: 0.0000e+00

Epoch 00124: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 126/1000
 - 0s - loss: 7.2147 - accuracy: 0.0375 - val_loss: 6.9826 - val_accuracy: 0.0000e+00

Epoch 00125: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 127/1000
 - 0s - loss: 7.1532 - accuracy: 0.0000e+00 - val_loss: 6.9870 - val_accuracy: 0.0000e+00

Epoch 00126: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 128/1000
 - 0s - loss: 6.9773 - accuracy: 0.0500 - val_loss: 6.9908 - val_accuracy: 0.0000e+00

Epoch 00127: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\D

Epoch 156/1000
 - 0s - loss: 7.1566 - accuracy: 0.0750 - val_loss: 7.0267 - val_accuracy: 0.0000e+00

Epoch 00155: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 157/1000
 - 0s - loss: 6.5724 - accuracy: 0.0750 - val_loss: 7.0281 - val_accuracy: 0.0000e+00

Epoch 00156: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 158/1000
 - 0s - loss: 6.8468 - accuracy: 0.0250 - val_loss: 7.0275 - val_accuracy: 0.0000e+00

Epoch 00157: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 159/1000
 - 0s - loss: 6.9111 - accuracy: 0.0625 - val_loss: 7.0282 - val_accuracy: 0.0000e+00

Epoch 00158: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Deskt

...

Epoch 774/1000
 - 0s - loss: 3.2036 - accuracy: 0.6750 - val_loss: 15.1296 - val_accuracy: 0.0000e+00

Epoch 00773: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 775/1000
 - 0s - loss: 3.0830 - accuracy: 0.7250 - val_loss: 15.1485 - val_accuracy: 0.0000e+00

Epoch 00774: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 776/1000
 - 0s - loss: 3.0899 - accuracy: 0.7250 - val_loss: 15.1700 - val_accuracy: 0.0000e+00

Epoch 00775: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 777/1000
 - 0s - loss: 3.0696 - accuracy: 0.6875 - val_loss: 15.1823 - val_accuracy: 0.0000e+00

Epoch 00776: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\D


Epoch 00803: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 805/1000
 - 0s - loss: 2.8213 - accuracy: 0.8000 - val_loss: 15.7476 - val_accuracy: 0.0000e+00

Epoch 00804: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 806/1000
 - 0s - loss: 2.9346 - accuracy: 0.7750 - val_loss: 15.7046 - val_accuracy: 0.0000e+00

Epoch 00805: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 807/1000
 - 0s - loss: 2.9341 - accuracy: 0.7500 - val_loss: 15.6718 - val_accuracy: 0.0000e+00

Epoch 00806: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 808/1000
 - 0s -

Epoch 835/1000
 - 0s - loss: 2.9301 - accuracy: 0.7500 - val_loss: 16.3199 - val_accuracy: 0.0000e+00

Epoch 00834: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 836/1000
 - 0s - loss: 2.7390 - accuracy: 0.8500 - val_loss: 16.4160 - val_accuracy: 0.0000e+00

Epoch 00835: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 837/1000
 - 0s - loss: 2.8415 - accuracy: 0.8250 - val_loss: 16.5098 - val_accuracy: 0.0000e+00

Epoch 00836: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 838/1000
 - 0s - loss: 2.8534 - accuracy: 0.7875 - val_loss: 16.5866 - val_accuracy: 0.0000e+00

Epoch 00837: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\D


Epoch 00864: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 866/1000
 - 0s - loss: 2.8848 - accuracy: 0.7750 - val_loss: 15.9003 - val_accuracy: 0.0000e+00

Epoch 00865: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 867/1000
 - 0s - loss: 2.7287 - accuracy: 0.8000 - val_loss: 15.9218 - val_accuracy: 0.0000e+00

Epoch 00866: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 868/1000
 - 0s - loss: 2.6912 - accuracy: 0.8375 - val_loss: 15.9362 - val_accuracy: 0.0000e+00

Epoch 00867: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 869/1000
 - 0s -

Epoch 896/1000
 - 0s - loss: 2.6090 - accuracy: 0.9250 - val_loss: 17.1698 - val_accuracy: 0.0000e+00

Epoch 00895: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 897/1000
 - 0s - loss: 2.7568 - accuracy: 0.8250 - val_loss: 17.2590 - val_accuracy: 0.0000e+00

Epoch 00896: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 898/1000
 - 0s - loss: 2.6369 - accuracy: 0.8750 - val_loss: 17.3445 - val_accuracy: 0.0000e+00

Epoch 00897: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\Desktop\active_learning\models\DiscriminativeLearned_Random_cifar10_100_1_0.hdf5
Epoch 899/1000
 - 0s - loss: 2.7042 - accuracy: 0.8375 - val_loss: 17.4139 - val_accuracy: 0.0000e+00

Epoch 00898: val_acc improved from 0.00000 to 0.00000, saving model to C:\Users\76113\D